In [1]:
import os
import requests
import requests
import ast

import pandas as pd
import glob
import plotly.express as px

from bs4 import BeautifulSoup

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

from time import sleep


from locations import *
from parsing import *

# LOCATIONS SCRAPING

In [2]:
# Base

base_url = 'https://www.pisos.com/'

venta_url = f'{base_url}venta/'

In [3]:
# Sacamos todas las paginas filtradas por provincias

response = requests.get(base_url)

soup = BeautifulSoup(response.text, "html.parser")

provincias_str = soup.find('div', class_ = 'home-container').find('div', class_ = 'selectBox').find_all('ul')[-1].text

provincias = [x.lower() for x in provincias_str.strip().split('\n')]

endpoints = replaceWithUnderscore(provincias)

endpoints = [venta_url + endpoint for endpoint in endpoints]

with open('locations.txt', 'w') as file:
    file.write('\n'.join(endpoints))

# SINGLE PAGE SCRAPING

In [4]:
def scrape(url):

    browser = webdriver.Chrome()
    browser.get(url)
    browser.maximize_window()

    element = WebDriverWait(browser, 10).until(
        EC.presence_of_element_located((By.XPATH, '//*[@id="didomi-notice-agree-button"]'))
    )

    element.click() # Accept cookies

    for i in range(30):

        element = WebDriverWait(browser, 10).until(
            EC.presence_of_element_located((By.XPATH, f'(//*[@id]/div[2]/div[1]/div[2]/a)[{i + 1}]'))
        )

        element.click() # Click on the first post

        # <SCROLLING>
        while True:
            is_at_bottom = browser.execute_script("return window.scrollY + window.innerHeight >= document.body.scrollHeight")
            browser.execute_script("window.scroll({ top: document.body.scrollHeight, behavior: 'smooth' });")
            if is_at_bottom:
                break
            sleep(0.2)
        # </SCROLLING>
        
        html_content = browser.page_source
        soft_url = url.replace('https://www.pisos.com/venta/', '')
        soft_url = soft_url.replace('/', '_')
        soft_url = soft_url.replace('-', '_')

        file_path = f'{os.getcwd()}/html_content/{soft_url}_{i}.html'
        try:
            with open(file_path, 'w', encoding='utf-8') as file:
                file.write(html_content)
        except Exception as e:
            with open(file_path, 'w', encoding='utf-8') as file:
                file.write(repr(e))

        go_back_element = WebDriverWait(browser, 10).until(
            EC.presence_of_element_located((By.XPATH, '//*[@id="GoBackLink"]'))
        )

        go_back_element.click() # Click on back arrow

    browser.quit()

    

# TESTING

In [5]:
def scanRegions(url):
    response = requests.get(url)

    print(f'URL: {url} | STATUS {response.status_code}')

    soup = BeautifulSoup(response.text, 'html.parser')

    items = soup.select('div.zoneList a.item:not(.item-subitem)')

    endpoints = {}
    for item in items:
        endpoint = item['href']
        n_results = item.find('span', class_ = 'total').text

        # <INT>
        if len(n_results) != 0:
            try:
                n_results = n_results[1:-1]
                n_results = ''.join(n_results.split('.'))
                n_results = int(n_results)
            except:
                print(f'FAIL CASTING TO INTEGER {endpoint}')
        else:
            print(f'n_results EMPTY {endpoint}')
        #</INT>

        # <RECURSSION>
        if n_results > 3000:
            endpoints[endpoint] = scanRegions(base_url[:-1] + endpoint)
        # </RECURSSION>

        else: endpoints[endpoint] = n_results

    return endpoints

In [6]:
def parseRegions(endpoints):

    def extract(endpoints):
        array = []
        for key, value in endpoints.items():
            if isinstance(value, int):
                array.append(key)
                continue

            data = extract(value)
            array.extend(data)

        return array
    
    endpoints = extract(endpoints)

    array = []
    
    for endpoint in endpoints:
        data = endpoint
        if '/venta/pisos-' in endpoint:
            data = endpoint.replace('/venta/pisos-', '/viviendas/')
        array.append(data)

    return array


In [7]:
# URL = 'https://www.pisos.com/viviendas/barcelona/'

# urls = scanRegions(URL)
# urls = parseRegions(urls)
# urls = [base_url + x for x in urls]
# urls = [x.replace('d//vivienas/', '/venta/pisos-') for x in urls]

In [8]:
# for url in urls:
#     for i in range(57):
#         try:
#             endpoint = url + f'{i+1}'
#             scrape(endpoint)
#         except:
#             continue

In [9]:
# data = {
#     'price' : [],
#     'title' : [],
#     'location' : [],
#     'lat' : [],
#     'lng' : [],
#     'characteristics' : [],
# }

# files = glob.glob('html_content/*.html')

# for file in files:
#     with open(file, encoding='utf-8') as f:
#         source = f.read()
#     soup = BeautifulSoup(source, 'html.parser')

#     price = getPrice(soup)
#     title = getTitle(soup)
#     location = getLocation(soup)
#     lat, long = getLatLong(soup)
#     characteristics = getCharacteristics(soup)

#     data['price'].append(price)
#     data['title'].append(title)
#     data['location'].append(location)
#     data['lat'].append(lat)
#     data['lng'].append(long)
#     data['characteristics'].append(characteristics)

# df = pd.DataFrame(data)

In [10]:
df = pd.read_csv('prueba.csv')

In [11]:
def tryInt(n):
    try:
        return int(n)
    except: return np.nan

In [12]:
prices = df[['price']].applymap(lambda x: tryInt(''.join(x[:-2].split('.'))))

C:\Users\cuicuidev\AppData\Local\Temp\ipykernel_43980\2714858502.py:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  prices = df[['price']].applymap(lambda x: tryInt(''.join(x[:-2].split('.'))))


In [24]:
px.histogram(prices, nbins=800)

In [42]:
cadenas = df['characteristics'].iloc

In [61]:
df['characteristics'] = df['characteristics'].apply(ast.literal_eval)

price                                              title  \
0     180.000 €        Finca rústica en venta en Calle Lugar Babio   
1     210.000 €              Casa en venta en Calle Punta Do Salto   
2     126.626 €                Piso en venta en Calle Blanco White   
3     102.600 €               Piso en venta en Calle del Roi Xordo   
4      95.000 €             Piso en venta en Travesía de Pastoriza   
...         ...                                                ...   
4214  479.900 €                   Casa en venta en Calle Casteliño   
4215  145.000 €                  Piso en venta en Calle de la obra   
4216  134.000 €  Casa unifamiliar en venta en Avenida de Sada y...   
4217  380.000 €         Chalet unifamiliar en venta en Soneiro,  1   
4218  135.000 €               Piso en venta en Camiño de Ferrer, 5   

                                               location        lat       lng  \
0       Calle Lugar Babio. Bergondo (Carrio) (Bergondo)  43.317188 -8.243459   
1                         Calle Punta Do Salto. Arteixo  43.340884 -8.482044   
2     Calle Blanco White. Os Mallos-A Falperra (A Co...  43.347553 -8.416538   
3                        Calle del Roi Xordo. Culleredo  43.318661 -8.384513   
4                        Travesía de Pastoriza. Arteixo  43.336506 -8.462301   
...                                                 ...        ...       ...   
4214                              Calle Casteliño. Sada  43.339523 -8.267679   
4215                             Calle de la obra. Sada  43.348638 -8.251601   
4216  Avenida de Sada y sus Contornos, 44, cerca de ...  43.358830 -8.251664   
4217                      Soneiro,  1. Alborelle (Sada)  43.327100 -8.287360   
4218                 Camiño de Ferrer, 5. Fontán (Sada)  43.351033 -8.262322   

                                        characteristics  
0     [Superficie construida : 445 m², Superficie út...  
1     [Superficie construida : 420 m², Superficie út...  
2     [Superficie construida : 78 m², Habitaciones :...  
3     [Superficie construida : 104 m², Habitaciones ...  
4     [Superficie construida : 93 m², Superficie úti...  
...                                                 ...  
4214  [Superficie construida : 465 m², Superficie út...  
4215  [Superficie construida : 102 m², Habitaciones ...  
4216  [Superficie construida : 87 m², Habitaciones :...  
4217  [Superficie construida : 1.300 m², Superficie ...  
4218  [Superficie construida : 78 m², Superficie úti...  

[4219 rows x 6 columns]

In [63]:
characteristics = df['characteristics'].iloc

In [64]:
columnas = []

for chars in characteristics:
    for char in chars:
        vals = char.split(':')
        if isinstance(vals, list):
            columnas.append(vals[0])
        else:
            columnas.append(vals)

columnas = [x.strip() for x in columnas]
columnas = list(set(columnas))

In [91]:
dict_columns = {}
for column in columnas:
    dict_columns[column] = []

In [94]:
for chars in characteristics:
    for char in chars:
        vals = char.split(':')
        if len(vals) == 2:
            key, value = vals
        else:
            key, value = vals[0], np.nan

        key = key.strip()
#####################
NO FUNCUONASJDASJKDJKHASKLDJAS
    for col in columnas:
        print(key, col)
        if key == col:
            dict_columns[col].append(value)
        else:
            dict_columns[col].append(np.nan)

Pedir más información Chimenea
Pedir más información Se aceptan mascotas
Pedir más información Superficie solar
Pedir más información Urbanizado
Pedir más información Tipo de casa
Pedir más información Interior
Pedir más información Portero automático
Pedir más información Referencia
Pedir más información Antigüedad
Pedir más información Ascensor
Pedir más información Puerta blindada
Pedir más información Cocina
Pedir más información Cocina equipada
Pedir más información Tipo suelo
Pedir más información Clasificación
Pedir más información Sistema de seguridad
Pedir más información Pedir más información
Pedir más información Superficie útil
Pedir más información Calle alumbrada
Pedir más información Exterior
Pedir más información Carpintería interior
Pedir más información Vidrios dobles
Pedir más información Gas
Pedir más información Agua
Pedir más información Jardín
Pedir más información Teléfono
Pedir más información Calle asfaltada
Pedir más información Emisiones
Pedir más informació

In [93]:
pd.DataFrame(dict_columns)

Chimenea Se aceptan mascotas Superficie solar       Urbanizado  \
0     dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
1     dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
2     dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
3     dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
4     dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
...               ...                 ...              ...              ...   
4214  dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
4215  dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
4216  dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
4217  dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
4218  dasljkdjkasdjka     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   

         Tipo de casa         Interior Portero automático       Referencia  \
0     dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
1     dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
2     dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
3     dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
4     dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
...               ...              ...                ...              ...   
4214  dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
4215  dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
4216  dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
4217  dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   
4218  dasljkdjkasdjka  dasljkdjkasdjka    dasljkdjkasdjka  dasljkdjkasdjka   

           Antigüedad         Ascensor  ...      Calefacción  \
0     dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
1     dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
2     dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
3     dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
4     dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
...               ...              ...  ...              ...   
4214  dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
4215  dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
4216  dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
4217  dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   
4218  dasljkdjkasdjka  dasljkdjkasdjka  ...  dasljkdjkasdjka   

     Gastos de comunidad          Consumo Armarios empotrados  \
0        dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
1        dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
2        dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
3        dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
4        dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
...                  ...              ...                 ...   
4214     dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
4215     dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
4216     dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
4217     dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   
4218     dasljkdjkasdjka  dasljkdjkasdjka     dasljkdjkasdjka   

             Trastero           Garaje      Orientación              Luz  \
0     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
1     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
2     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
3     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
4     dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka  dasljkdjkasdjka   
...               ...              ...              ...              ...   
4214  dasljkdjkasdjka  dasljkdjkasdjka  daslj

In [ ]:
df['superficie_construida'] = df['characteristics'].apply(lambda x: x['superficie_construida'])